# **Closer look on Titles of Popular Videos**

[spaCy](https://spacy.io/usage/spacy-101) is a free, open-source library for advanced Natural Language Processing (NLP) in Python. 

> "Tokens" are usually individual words (at least in languages like English) and "tokenization" is taking a text or set of text and breaking it up into individual its words. These tokens are then used as the input for other types of analysis or tasks, like parsing (automatically tagging the syntactic relationship between words). We need to tokenize word so that we can use it for our title generating model/other cool analysis ([source](https://www.kaggle.com/rtatman/tokenization-tutorial))

In [23]:
#simple example 

nlp = spacy.load("en_core_web_sm")
doc = nlp(u"An apple is not a banana")
for token in doc:
    print(token.text)

An
apple
is
not
a
banana



<table>
<tr><td>0 </td><td> 1 </td> <td>2 </td><td>3 </td><td>4 </td> <td>5 </td></tr>
<tr><td>An </td> <td>  apple</td><td>  is</td><td>not </td> <td>  a</td><td> banana</td></tr>
</table>

In [24]:
punctuations = string.punctuation
stopwords = list(STOP_WORDS)
parser = English()

def spacy_tokenizer(sentence):
    mytokens = parser(sentence)
    mytokens = [ word.lemma_.lower().strip() if word.lemma_ != "-PRON-" else word.lower_ for word in mytokens ]
    mytokens = [ word for word in mytokens if word not in stopwords and word not in punctuations ]
    mytokens = " ".join([i for i in mytokens])
    return mytokens


tqdm.pandas()

normal = three_countries["title"][three_countries["popular"] == 0].progress_apply(spacy_tokenizer)
popular = three_countries["title"][three_countries["popular"] == 1].progress_apply(spacy_tokenizer)

100%|██████████| 2866/2866 [00:02<00:00, 973.33it/s] 


In [25]:
#tokenize words by popularity 

def word_generator(text):
    word = list(text.split())
    return word
def bigram_generator(text):
    bgram = list(nltk.bigrams(text.split()))
    bgram = [' '.join((a, b)) for (a, b) in bgram]
    return bgram
def trigram_generator(text):
    tgram = list(nltk.trigrams(text.split()))
    tgram = [' '.join((a, b, c)) for (a, b, c) in tgram]
    return tgram


normal_words = normal.progress_apply(word_generator)
popular_words = popular.progress_apply(word_generator)
normal_bigrams = normal.progress_apply(bigram_generator)
popular_bigrams = popular.progress_apply(bigram_generator)
normal_trigrams = normal.progress_apply(trigram_generator)
popular_trigrams = popular.progress_apply(trigram_generator)

100%|██████████| 2866/2866 [00:00<00:00, 85867.69it/s]


In [26]:
#function that makes a pretty word frequency plot

def word_plot(words,my_color):
    slist =[]
    for x in words:
        slist.extend(x)
    fig = plt.figure(figsize=(15, 10))
    pd.Series(slist).value_counts()[:20].sort_values(ascending=True).plot(kind='barh',fontsize=20, color=my_color)
    plt.show()


In [27]:
word_plot(popular_words,'blue')


In [28]:
word_plot(popular_bigrams,'orange')


In [29]:
word_plot(popular_trigrams,'red')

### TfidfVectorizer

Tf-idf analyzes the impact of tokens (words) throughout the whole documents. For example, the more times a word appears in a document (each title), the more weight it will have. However, the more documents (titles) the word appears in, it is 'penalized' and the weight is diminished because it is empirically less informative than features that occur in a small fraction of the training corpus ([source](https://www.kaggle.com/adamschroeder/countvectorizer-tfidfvectorizer-predict-comments))

* tf(t)= the term frequency is the number of times the term appears in the document
* idf(d, t) = the document frequency is the number of documents 'd' that contain term 't'

#### For example, the word "banana" appears all documents , so its idf is the lowest

In [30]:
txt1 = ['I like banana', 'An apple is not a banana', 'banana banana oh banana']
tf = TfidfVectorizer(smooth_idf=False, sublinear_tf=False, norm=None, analyzer='word')
txt_fitted = tf.fit(txt1)
txt_transformed = txt_fitted.transform(txt1)
print ("The text: ", txt1)

The text:  ['I like banana', 'An apple is not a banana', 'banana banana oh banana']


In [31]:
tf.vocabulary_

{'like': 4, 'banana': 2, 'an': 0, 'apple': 1, 'is': 3, 'not': 5, 'oh': 6}

In [32]:
idf = tf.idf_
print(dict(zip(txt_fitted.get_feature_names(), idf)))
print("\nThe token 'banana' appears 5 times but it is also in all documents, so its idf is the lowest")

{'an': 2.09861228866811, 'apple': 2.09861228866811, 'banana': 1.0, 'is': 2.09861228866811, 'like': 2.09861228866811, 'not': 2.09861228866811, 'oh': 2.09861228866811}

The token 'banana' appears 5 times but it is also in all documents, so its idf is the lowest


In [33]:
word_vectorizer = TfidfVectorizer(
    sublinear_tf=True,
    strip_accents='unicode',
    analyzer='word',
    token_pattern=r'\w{1,}',
    stop_words='english',
    ngram_range=(1, 1),
    max_features=10000)
word_vectorizer.fit(three_countries.title)
word_features = word_vectorizer.transform(three_countries.title)

classifier_popular = LogisticRegression(C=0.1, solver='sag')
classifier_popular.fit(word_features ,three_countries.popular)


LogisticRegression(C=0.1, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='warn',
          n_jobs=None, penalty='l2', random_state=None, solver='sag',
          tol=0.0001, verbose=0, warm_start=False)

In [34]:
names=['normal','popular']

In [35]:
c_tf = make_pipeline( word_vectorizer,classifier_popular)
explainer_tf = LimeTextExplainer(class_names=names)

exp = explainer_tf.explain_instance(three_countries.title.iloc[10], c_tf.predict_proba, num_features=4, top_labels=1)
exp.show_in_notebook(text=three_countries.title.iloc[10])


In [36]:
exp = explainer_tf.explain_instance(three_countries.title.iloc[4], c_tf.predict_proba, num_features=5, top_labels=1)
exp.show_in_notebook(text=three_countries.title.iloc[4])

In [37]:
exp = explainer_tf.explain_instance(three_countries.title.iloc[10035], c_tf.predict_proba, num_features=5, top_labels=1)
exp.show_in_notebook(text=three_countries.title.iloc[10035])

In [38]:
import plotly.plotly as py
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.figure_factory as ff
import plotly.tools as tls


labels = list(three_countries.category_names.value_counts().index.values)
values = list(three_countries.category_names.value_counts().values)

trace = go.Pie(labels=labels, values=values)

iplot([trace], filename='basic_pie_chart')

In [39]:
three_countries.groupby('category_names')['views'].describe()

count          mean     ...            75%         max
category_names                                 ...                           
Autos & Vehicles       310.0  3.188070e+05     ...      480935.00   1992282.0
Comedy                2305.0  5.366228e+05     ...      648648.00  12924004.0
Education              763.0  2.852218e+05     ...      326820.50  12100921.0
Entertainment         9730.0  4.598304e+05     ...      451687.25  37736281.0
Film & Animation      1431.0  4.938655e+05     ...      473297.50  15969920.0
Gaming                 966.0  4.992588e+05     ...      531995.25  15919643.0
Howto & Style         1780.0  3.806085e+05     ...      407440.50   8307705.0
Movies                   1.0  2.255280e+05     ...      225528.00    225528.0
Music                 2479.0  1.230716e+06     ...      976700.00  47669287.0
News & Politics       3414.0  2.095382e+05     ...      213227.75   5943011.0
People & Blogs        3072.0  3.547916e+05     ...      363105.25  20921796.0
Pets & Animals         325.0  3.150967e+05     ...      360901.00   5954189.0
Science & Technology   900.0  4.894011e+05     ...      599272.00  15316016.0
Shows                  106.0  5.252397e+05     ...      627156.25    997580.0
Sports                2422.0  5.219269e+05     ...      605685.25  15860214.0
Travel & Events        247.0  2.338437e+05     ...      252116.00   3209475.0

[16 rows x 8 columns]

## Latent Dirichlet Allocation (LDA) by Category

In [40]:
entertainment_title= three_countries["title"][(three_countries['category_names'] == 'Entertainment')] 
news_politics_title= three_countries["title"][(three_countries['category_names'] == 'News & Politics')] 
people_title= three_countries["title"][(three_countries['category_names'] == 'People & Blogs')] 
music_title= three_countries["title"][(three_countries['category_names'] == 'Music')] 
sports_title= three_countries["title"][(three_countries['category_names'] == 'Sports')] 
comedy_title= three_countries["title"][(three_countries['category_names'] == 'Comedy')] 

In [41]:
vectorizer_entertainment_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
entertainment_title_vectorized = vectorizer_entertainment_title.fit_transform(entertainment_title)
lda_popular_entertainment_title_vectorized = LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
entertainment_title_vectorized_lda = lda_popular_entertainment_title_vectorized.fit_transform(entertainment_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_popular_entertainment_title_vectorized,entertainment_title_vectorized, vectorizer_entertainment_title, mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
0      -13.210489  -15.640155       1        1  15.337165
5     -131.283585   89.782860       2        1  15.294792
3     -163.545639  -65.183716       3        1  15.228728
2       19.051882  139.326004       4        1  14.029008
6      104.863083 -121.062248       5        1  13.966568
1      137.125107   33.903568       6        1  13.592852
4      -45.472019 -170.606827       7        1  12.550886, topic_info=     Category         Freq        Term        Total  loglift  logprob
term                                                                 
569   Default  1466.000000     episode  1466.000000  30.0000  30.0000
1595  Default   337.000000      season   337.000000  29.0000  29.0000
515   Default   292.000000       drama   292.000000  28.0000  28.0000
1854  Default   291.000000     trailer   291.000000  27.0000  27.0000
1251  Default   226.000000         new   226.000000  26.0000  26.0000
1280  Default   292.000000    official   292.000000  25.0000  25.0000
942   Default   189.000000        juan   189.000000  24.0000  24.0000
177   Default   194.000000        best   194.000000  23.0000  23.0000
1610  Default   184.000000      series   184.000000  22.0000  22.0000
1924  Default   153.000000       video   153.000000  21.0000  21.0000
303   Default   168.000000   challenge   168.000000  20.0000  20.0000
1779  Default   156.000000       taste   156.000000  19.0000  19.0000
1402  Default   144.000000       promo   144.000000  18.0000  18.0000
1706  Default   154.000000        star   154.000000  17.0000  17.0000
403   Default   141.000000       crime   141.000000  16.0000  16.0000
1329  Default   138.000000      patrol   138.000000  15.0000  15.0000
118   Default   134.000000   australia   134.000000  14.0000  14.0000
1070  Default   140.000000        live   140.000000  13.0000  13.0000
1438  Default   132.000000        rani   132.000000  12.0000  12.0000
1909  Default   131.000000       vaani   131.000000  11.0000  11.0000
1871  Default   124.000000       trump   124.000000  10.0000  10.0000
1315  Default   132.000000     parents   132.000000   9.0000   9.0000
481   Default   122.000000     digital   122.000000   8.0000   8.0000
1215  Default   143.000000       movie   143.000000   7.0000   7.0000
1667  Default   108.000000         snl   108.000000   6.0000   6.0000
103   Default   115.000000         ary   115.000000   5.0000   5.0000
1292  Default   107.000000      ooltah   107.000000   4.0000   4.0000
1160  Default   107.000000       mehta   107.000000   3.0000   3.0000
318   Default   107.000000    chashmah   107.000000   2.0000   2.0000
1766  Default   107.000000      taarak   107.000000   1.0000   1.0000
...       ...          ...         ...          ...      ...      ...
743    Topic7    96.952563         got    97.756965   2.0671  -3.8811
861    Topic7    84.727131         hum    85.531654   2.0659  -4.0159
1769   Topic7    80.601353      talent    81.404856   2.0655  -4.0658
156    Topic7    76.654592      battle    77.459196   2.0649  -4.1160
1330   Topic7    69.220730        paul    70.024259   2.0638  -4.2181
996    Topic7    64.817774     kitchen    65.621276   2.0631  -4.2838
853    Topic7    56.922620       house    57.727177   2.0613  -4.4137
1282   Topic7    53.590739         old    54.395624   2.0605  -4.4740
649    Topic7    51.940380      finale    52.746004   2.0600  -4.5053
991    Topic7    51.611926         kim    52.417294   2.0599  -4.5116
906    Topic7    48.699731       james    49.504171   2.0590  -4.5697
1074   Topic7    48.168856       logan    48.972368   2.0588  -4.5806
850    Topic7    48.125774       hotel    48.929395   2.0588  -4.5815
1261   Topic7    43.160406  nightmares    43.963626   2.0569  -4.6904
1451   Topic7    43.132472    reaction    43.936810   2.0569  -4.6911
1557   Topic7    42.614487      saison    43.417764   2.0567  -4.7032
742  

In [42]:
vectorizer_news_politics_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
news_politics_title_vectorized = vectorizer_news_politics_title.fit_transform(news_politics_title)
lda_news_politics_title_vectorized= LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
news_politics_title_vectorized_lda = lda_news_politics_title_vectorized.fit_transform(news_politics_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_news_politics_title_vectorized,news_politics_title_vectorized, vectorizer_news_politics_title , mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
2      159.853775  -27.017454       1        1  20.323634
1      -55.589111 -126.181152       2        1  17.485332
4      102.601761   97.367516       3        1  15.431528
0       80.758476 -138.791275       4        1  12.109680
3       23.505898  -14.406333       5        1  11.925120
6      -33.745235  109.980148       6        1  11.586369
5     -112.840843   -1.794492       7        1  11.138336, topic_info=     Category        Freq        Term       Total  loglift  logprob
term                                                               
816   Default  555.000000       trump  555.000000  30.0000  30.0000
461   Default  164.000000        live  164.000000  29.0000  29.0000
538   Default  156.000000       msnbc  156.000000  28.0000  28.0000
552   Default  223.000000        news  223.000000  27.0000  27.0000
618   Default  153.000000   president  153.000000  26.0000  26.0000
814   Default   87.000000     trudeau   87.000000  25.0000  25.0000
551   Default  107.000000         new  107.000000  24.0000  24.0000
221   Default  107.000000      donald  107.000000  23.0000  23.0000
498   Default   72.000000      meghan   72.000000  22.0000  22.0000
363   Default   90.000000       house   90.000000  21.0000  21.0000
336   Default   66.000000      hawaii   66.000000  20.0000  20.0000
239   Default   78.000000     episode   78.000000  19.0000  19.0000
857   Default   81.000000       watch   81.000000  18.0000  18.0000
865   Default   74.000000       white   74.000000  17.0000  17.0000
400   Default   78.000000         joe   78.000000  16.0000  16.0000
99    Default   68.000000    breaking   68.000000  15.0000  15.0000
849   Default   67.000000      wanted   67.000000  14.0000  14.0000
845   Default   57.000000     volcano   57.000000  13.0000  13.0000
685   Default   51.000000     sanders   51.000000  12.0000  12.0000
536   Default   72.000000     morning   72.000000  11.0000  11.0000
713   Default   60.000000      shahid   60.000000  10.0000  10.0000
636   Default   64.000000       radyo   64.000000   9.0000   9.0000
383   Default   59.000000   interview   59.000000   8.0000   8.0000
335   Default   51.000000       harry   51.000000   7.0000   7.0000
621   Default   50.000000      prince   50.000000   6.0000   6.0000
720   Default   63.000000    shooting   63.000000   5.0000   5.0000
486   Default   57.000000      masood   57.000000   4.0000   4.0000
594   Default   57.000000        paul   57.000000   3.0000   3.0000
480   Default   48.000000       march   48.000000   2.0000   2.0000
839   Default   49.000000       video   49.000000   1.0000   1.0000
...       ...         ...         ...         ...      ...      ...
184    Topic7   23.777535     daniels   24.603688   2.1606  -4.1189
5      Topic7   21.289329   -year-old   22.085689   2.1581  -4.2294
235    Topic7   20.949844         end   21.748543   2.1574  -4.2455
403    Topic7   22.982172       jones   23.891549   2.1560  -4.1529
494    Topic7   18.589852       media   19.386405   2.1528  -4.3650
875    Topic7   17.378259         won   18.173148   2.1501  -4.4324
871    Topic7   16.989043        wolf   17.788635   2.1488  -4.4551
260    Topic7   15.236056        fake   16.033189   2.1438  -4.5640
110    Topic7   14.291280  california   15.086301   2.1406  -4.6280
824    Topic7   14.088582      tweets   14.882613   2.1399  -4.6423
631    Topic7   13.923615   questions   14.717988   2.1393  -4.6541
364    Topic7   13.878648    huckabee   14.672295   2.1392  -4.6573
247    Topic7   13.803185   exclusive   14.599064   2.1387  -4.6627
702    Topic7   13.191178         sen   13.986729   2.1362  -4.7081
640    Topic7   15.493866      reacts   16.435636   2.1358  -4.5472
399    Topic7   12.297132         jim   13.091537   2.1322  -4.7783
52     Topic7   12.273784       asked   13.068349   2.1320  -4.7802
654    Topic7   12.155614    report

In [43]:
vectorizer_people_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
people_title_vectorized = vectorizer_people_title.fit_transform(people_title)
lda_people_title_vectorized= LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
people_title_vectorized_lda = lda_people_title_vectorized.fit_transform(people_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_people_title_vectorized,people_title_vectorized, vectorizer_people_title , mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
1     -115.411278  184.910706       1        1  17.189495
4      133.982452 -147.876282       2        1  16.826294
2        9.283088   18.518837       3        1  15.062050
6      -72.464500 -172.669891       4        1  13.385991
5     -197.165405   -6.278510       5        1  12.832366
3      215.732513   43.308674       6        1  12.672312
0       91.040390  209.704880       7        1  12.031492, topic_info=     Category        Freq        Term       Total  loglift  logprob
term                                                               
165   Default  129.000000     episode  129.000000  30.0000  30.0000
571   Default  126.000000       trump  126.000000  29.0000  29.0000
282   Default   97.000000         joe   97.000000  28.0000  28.0000
556   Default   93.000000        time   93.000000  27.0000  27.0000
479   Default   93.000000       rogan   93.000000  26.0000  26.0000
396   Default   92.000000         new   92.000000  25.0000  25.0000
41    Default   81.000000        best   81.000000  24.0000  24.0000
397   Default   76.000000        news   76.000000  23.0000  23.0000
121   Default   68.000000         day   68.000000  22.0000  22.0000
88    Default   53.000000   christmas   53.000000  21.0000  21.0000
589   Default   50.000000       video   50.000000  20.0000  20.0000
590   Default   55.000000        view   55.000000  19.0000  19.0000
171   Default   52.000000  experience   52.000000  18.0000  18.0000
144   Default   51.000000       drama   51.000000  17.0000  17.0000
404   Default   40.000000    official   40.000000  16.0000  16.0000
420   Default   38.000000        paul   38.000000  15.0000  15.0000
573   Default   36.000000         try   36.000000  14.0000  14.0000
263   Default   40.000000         hum   40.000000  13.0000  13.0000
305   Default   37.000000         kol   37.000000  12.0000  12.0000
65    Default   37.000000         bts   37.000000  11.0000  11.0000
466   Default   30.000000        real   30.000000  10.0000  10.0000
281   Default   30.000000       jimmy   30.000000   9.0000   9.0000
82    Default   30.000000   challenge   30.000000   8.0000   8.0000
301   Default   29.000000      kimmel   29.000000   7.0000   7.0000
179   Default   28.000000      family   28.000000   6.0000   6.0000
583   Default   27.000000        ukur   27.000000   5.0000   5.0000
204   Default   28.000000     frontal   28.000000   4.0000   4.0000
208   Default   29.000000        game   29.000000   3.0000   3.0000
600   Default   28.000000       warda   28.000000   2.0000   2.0000
505   Default   28.000000      shamya   28.000000   1.0000   1.0000
...       ...         ...         ...         ...      ...      ...
508    Topic7   18.858615     sheldon   19.657314   2.0762  -3.9089
324    Topic7   20.641671        live   21.536577   2.0752  -3.8186
463    Topic7   17.623877    reaction   18.446339   2.0720  -3.9766
311    Topic7   13.947959      latest   14.744054   2.0621  -4.2106
284    Topic7   13.089180      jordan   13.888024   2.0584  -4.2741
427    Topic7   13.086005        phil   13.893962   2.0577  -4.2744
602    Topic7   12.722972       watch   13.518719   2.0570  -4.3025
408    Topic7   12.481848     opening   13.279779   2.0557  -4.3216
397    Topic7   71.406950        news   76.039333   2.0548  -2.5775
133    Topic7   10.913537      disney   11.715723   2.0467  -4.4559
435    Topic7   10.817789        play   11.614457   2.0466  -4.4647
38     Topic7   10.706382      beauty   11.502060   2.0460  -4.4751
561    Topic7   10.626069     tonight   11.421586   2.0454  -4.4826
120    Topic7   10.591081       david   11.387108   2.0452  -4.4859
387    Topic7   10.296355       msnbc   11.094045   2.0430  -4.5141
148    Topic7    9.764526     duterte   10.559329   2.0394  -4.5671
418    Topic7    9.690548     parents   10.486246   2.0387  -4.5748
459    Topic7    9.469836      rach

In [44]:
vectorizer_music_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
music_title_vectorized = vectorizer_music_title.fit_transform(music_title)
lda_music_title_vectorized= LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
music_title_vectorized_lda = lda_music_title_vectorized.fit_transform(music_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_music_title_vectorized,music_title_vectorized, vectorizer_music_title , mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=               x          y  topics  cluster       Freq
topic                                                  
6     -33.480179 -28.894712       1        1  29.037988
3      41.543434  52.538517       2        1  18.912765
5      20.537504 -41.023411       3        1  13.476359
1       4.031477  11.822059       4        1  12.082981
2     -49.987427  23.950117       5        1  10.005103
4      58.049610  -0.306757       6        1   8.828084
0     -12.475110  64.666832       7        1   7.656720, topic_info=     Category        Freq        Term       Total  loglift  logprob
term                                                               
396   Default  542.000000    official  542.000000  30.0000  30.0000
576   Default  591.000000       video  591.000000  29.0000  29.0000
510   Default  221.000000        song  221.000000  28.0000  28.0000
434   Default  162.000000     punjabi  162.000000  27.0000  27.0000
511   Default  211.000000       songs  211.000000  26.0000  26.0000
288   Default  152.000000      latest  152.000000  25.0000  25.0000
20    Default  235.000000       audio  235.000000  24.0000  24.0000
89    Default  108.000000   christmas  108.000000  23.0000  23.0000
320   Default  107.000000        love  107.000000  22.0000  22.0000
378   Default  305.000000       music  305.000000  21.0000  21.0000
311   Default  138.000000        live  138.000000  20.0000  20.0000
24    Default   49.000000      awards   49.000000  19.0000  19.0000
64    Default   50.000000         bts   50.000000  18.0000  18.0000
325   Default   48.000000      lyrics   48.000000  17.0000  17.0000
4     Default   54.000000       album   54.000000  16.0000  16.0000
384   Default   91.000000         new   91.000000  15.0000  15.0000
324   Default   84.000000       lyric   84.000000  14.0000  14.0000
44    Default   44.000000        best   44.000000  13.0000  13.0000
50    Default   35.000000   billboard   35.000000  12.0000  12.0000
418   Default   38.000000       piano   38.000000  11.0000  11.0000
305   Default   56.000000         lil   56.000000  10.0000  10.0000
543   Default   31.000000      teaser   31.000000   9.0000   9.0000
348   Default   28.000000  marshmello   28.000000   8.0000   8.0000
448   Default   42.000000     records   42.000000   7.0000   7.0000
453   Default   44.000000       remix   44.000000   6.0000   6.0000
491   Default   27.000000       shawn   27.000000   5.0000   5.0000
355   Default   27.000000      mendes   27.000000   4.0000   4.0000
101   Default   36.000000       cover   36.000000   3.0000   3.0000
397   Default   23.000000    officiel   23.000000   2.0000   2.0000
85    Default   28.000000     charlie   28.000000   1.0000   1.0000
...       ...         ...         ...         ...      ...      ...
92     Topic7   17.623385        clip   18.502708   2.5209  -3.7305
380    Topic7   16.761107         nct   17.688150   2.5158  -3.7807
497    Topic7   15.758740         sia   16.631491   2.5157  -3.8423
247    Topic7   14.442283       jimmy   15.316853   2.5108  -3.9296
10     Topic7   16.171384    american   17.179066   2.5091  -3.8165
476    Topic7   12.420872         sam   13.320110   2.4997  -4.0803
560    Topic7   11.203161       troye   12.091397   2.4933  -4.1835
504    Topic7   11.203285       sivan   12.091914   2.4933  -4.1835
558    Topic7   10.153267     tribute   11.030407   2.4867  -4.2819
381    Topic7    9.997206        need   10.870877   2.4858  -4.2974
148    Topic7    9.856172         eng   10.728751   2.4848  -4.3116
409    Topic7    8.791874        paul    9.664640   2.4749  -4.4259
589    Topic7    8.828406     wedding    9.707403   2.4747  -4.4217
196    Topic7    8.883865      grammy    9.778806   2.4736  -4.4155
215    Topic7    8.710586         hey    9.590409   2.4734  -4.4352
539    Topic7    8.798476       talks    9.696165   2.4724  -4.4251
533    Topic7    8.003539       super    8.877370   2.4660  -4.5198
34     Topic7    8.040686        band    8.919897   2

In [45]:
vectorizer_sports_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
sports_title_vectorized = vectorizer_sports_title.fit_transform(sports_title)
lda_sports_title_vectorized= LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
sports_title_vectorized_lda = lda_sports_title_vectorized.fit_transform(sports_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_sports_title_vectorized,sports_title_vectorized, vectorizer_sports_title , mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
6       57.194595 -196.158997       1        1  24.582273
1     -117.158302 -139.360138       2        1  15.357669
2      193.558853  -73.562965       3        1  13.891994
3      -18.782578  162.627701       4        1  13.104966
5      155.570831  105.830338       5        1  12.140356
0     -155.148102   40.032665       6        1  10.843632
4       19.206022  -16.765221       7        1  10.079109, topic_info=     Category        Freq        Term       Total  loglift  logprob
term                                                               
199   Default  543.000000        game  543.000000  30.0000  30.0000
233   Default  505.000000  highlights  505.000000  29.0000  29.0000
371   Default  386.000000         nba  386.000000  28.0000  28.0000
171   Default  184.000000        espn  184.000000  27.0000  27.0000
207   Default  137.000000       goals  137.000000  26.0000  26.0000
73    Default  181.000000   cavaliers  181.000000  25.0000  25.0000
301   Default  172.000000      lebron  172.000000  24.0000  24.0000
536   Default  111.000000     stephen  111.000000  23.0000  23.0000
580   Default   93.000000         ufc   93.000000  22.0000  22.0000
299   Default   72.000000       leafs   72.000000  21.0000  21.0000
93    Default  122.000000   cleveland  122.000000  20.0000  20.0000
583   Default   79.000000  undisputed   79.000000  19.0000  19.0000
450   Default   71.000000         raw   71.000000  18.0000  18.0000
449   Default  149.000000     raptors  149.000000  17.0000  17.0000
532   Default   80.000000       state   80.000000  16.0000  16.0000
625   Default   66.000000         wwe   66.000000  15.0000  15.0000
328   Default   60.000000       maple   60.000000  14.0000  14.0000
256   Default  125.000000       james  125.000000  13.0000  13.0000
455   Default   59.000000        real   59.000000  12.0000  12.0000
566   Default  106.000000     toronto  106.000000  11.0000  11.0000
211   Default   88.000000      golden   88.000000  10.0000  10.0000
174   Default   63.000000    extended   63.000000   9.0000   9.0000
74    Default   56.000000        cavs   56.000000   8.0000   8.0000
419   Default   84.000000    playoffs   84.000000   7.0000   7.0000
600   Default  153.000000    warriors  153.000000   6.0000   6.0000
496   Default  162.000000      season  162.000000   5.0000   5.0000
521   Default   52.000000       smith   52.000000   4.0000   4.0000
333   Default   49.000000       match   49.000000   3.0000   3.0000
25    Default   62.000000        ball   62.000000   2.0000   2.0000
341   Default   43.000000    mcgregor   43.000000   1.0000   1.0000
...       ...         ...         ...         ...      ...      ...
343    Topic7   16.111849       medal   16.954290   2.2437  -4.3212
23     Topic7   14.878556     babcock   15.702486   2.2408  -4.4009
152    Topic7   14.120619        dunk   14.944920   2.2380  -4.4531
515    Topic7   13.635377       skate   14.474144   2.2350  -4.4881
335    Topic7   13.004269    matthews   13.829559   2.2332  -4.5355
582    Topic7   12.866075  underwater   13.694854   2.2323  -4.5462
565    Topic7   12.949634         tor   13.784941   2.2322  -4.5397
458    Topic7   12.648318      record   13.482057   2.2309  -4.5633
365    Topic7   12.645409     morning   13.480116   2.2308  -4.5635
457    Topic7   12.258593       recap   13.082396   2.2297  -4.5946
305    Topic7   11.906128         lfr   12.741479   2.2269  -4.6237
612    Topic7   12.096226      winner   12.946785   2.2268  -4.6079
240    Topic7   11.119191        home   11.943335   2.2232  -4.6921
467    Topic7   10.457111       river   11.281556   2.2188  -4.7535
452    Topic7   10.325897    reaction   11.154552   2.2175  -4.7661
196    Topic7   10.177866        free   11.000477   2.2170  -4.7806
20     Topic7    9.816959      auston   10.637944   2.2144  -4.8167
483    Topic7    9.759936         r

In [46]:
vectorizer_comedy_title = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
comedy_title_vectorized = vectorizer_comedy_title.fit_transform(comedy_title)
lda_comedy_title_vectorized= LatentDirichletAllocation(n_components=7, max_iter=5, learning_method='online',verbose=True)
comedy_title_vectorized_lda = lda_comedy_title_vectorized.fit_transform(comedy_title_vectorized )

pyLDAvis.enable_notebook()
dash = pyLDAvis.sklearn.prepare(lda_comedy_title_vectorized,comedy_title_vectorized, vectorizer_comedy_title , mds='tsne')
dash

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
1       44.240566   -7.835799       1        1  17.733143
4      -93.565361 -129.460159       2        1  15.950438
3     -129.992233   50.695412       3        1  15.351158
2      -25.979336   71.726456       4        1  13.901870
6       10.447598 -108.429192       5        1  13.404643
0      -59.772358  -28.866877       6        1  13.045450
5     -163.785324  -49.897938       7        1  10.613299, topic_info=     Category        Freq       Term       Total  loglift  logprob
term                                                              
77    Default  153.000000        day  153.000000  30.0000  30.0000
54    Default   98.000000    comment   98.000000  29.0000  29.0000
14    Default   87.000000     awards   87.000000  28.0000  28.0000
68    Default   81.000000      daily   81.000000  27.0000  27.0000
375   Default  116.000000      trump  116.000000  26.0000  26.0000
204   Default   57.000000       look   57.000000  25.0000  25.0000
49    Default   54.000000     closer   54.000000  24.0000  24.0000
371   Default   46.000000     trevor   46.000000  23.0000  23.0000
249   Default   45.000000       noah   45.000000  22.0000  22.0000
173   Default   37.000000      jimmy   37.000000  21.0000  21.0000
57    Default   43.000000      conan   43.000000  20.0000  20.0000
102   Default   46.000000      fails   46.000000  19.0000  19.0000
145   Default   38.000000       hart   38.000000  18.0000  18.0000
194   Default   37.000000        les   37.000000  17.0000  17.0000
41    Default   40.000000  challenge   40.000000  16.0000  16.0000
175   Default   34.000000       john   34.000000  15.0000  15.0000
184   Default   37.000000      kevin   37.000000  14.0000  14.0000
367   Default   32.000000       time   32.000000  13.0000  13.0000
246   Default   36.000000        new   36.000000  12.0000  12.0000
22    Default   39.000000       best   39.000000  11.0000  11.0000
101   Default   36.000000   failarmy   36.000000  10.0000  10.0000
292   Default   36.000000       real   36.000000   9.0000   9.0000
356   Default   32.000000        tbs   32.000000   8.0000   8.0000
386   Default   34.000000      video   34.000000   7.0000   7.0000
18    Default   24.000000        bad   24.000000   6.0000   6.0000
197   Default   22.000000       life   22.000000   5.0000   5.0000
191   Default   40.000000      laugh   40.000000   4.0000   4.0000
412   Default   21.000000       yiay   21.000000   3.0000   3.0000
254   Default   24.000000     oliver   24.000000   2.0000   2.0000
413   Default   23.000000    youtube   23.000000   1.0000   1.0000
...       ...         ...        ...         ...      ...      ...
18     Topic7   23.659658        bad   24.501621   2.2081  -3.0948
197    Topic7   21.486813       life   22.315276   2.2052  -3.1912
412    Topic7   20.864038       yiay   21.683158   2.2046  -3.2206
47     Topic7   18.658946  christmas   19.477991   2.2001  -3.3323
173    Topic7   35.500302      jimmy   37.285111   2.1940  -2.6891
234    Topic7   14.220735  monologue   15.040906   2.1870  -3.6039
188    Topic7   14.075334     kimmel   14.899097   2.1862  -3.6142
354    Topic7   13.556946      talks   14.384221   2.1838  -3.6517
342    Topic7   12.614251    stephen   13.455195   2.1785  -3.7238
200    Topic7   11.930994        lip   12.754635   2.1763  -3.7795
290    Topic7   11.393270    reading   12.217012   2.1733  -3.8256
16     Topic7   10.781167       baby   11.599769   2.1699  -3.8808
370    Topic7    9.720193        tre   10.545630   2.1616  -3.9844
2      Topic7    9.662682        aib   10.484756   2.1614  -3.9903
76     Topic7    9.406639      david   10.231193   2.1590  -4.0172
409    Topic7    9.263403      worst   10.082590   2.1583  -4.0325
269    Topic7    9.376353     pisode   10.208408   2.1580  -4.0204
174    Topic7    9.479308        joe   10.352875   2.1549  -4.0095
274    Topic7    8